1本のリードをユニット配列の variant を含めた塩基組成で表現して、それを使って overlap (filtering) を試みる。

In [53]:
%matplotlib inline
%config InlineBackend.figure_format = 'retina'
from IPython.display import display
import plotly.offline as py
py.init_notebook_mode(connected=True)
import plotly.io as pio
pio.templates.default = 'plotly_white'
import logging
import logzero
logzero.loglevel(logging.INFO)

In [2]:
dir_fname = 'work'
import os
os.chdir(dir_fname)

In [3]:
import numpy as np
from copy import copy
import pandas as pd
from BITS.clustering.seq import ClusteringSeq
from BITS.seq.align import EdlibRunner
from BITS.seq.consed import ConsedRunner
from BITS.util.io import save_pickle, load_pickle
from BITS.util.io import load_pickle, save_pickle
import numpy as np
import pandas as pd
from BITS.plot.plotly import make_hist, make_scatter, make_layout, show_plot
from BITS.clustering.seq import ClusteringSeq
import consed
from BITS.seq.align import EdlibRunner
from collections import Counter, defaultdict
from logzero import logger
from dataclasses import dataclass
from typing import List
import random
from copy import copy
from collections import Counter
from dataclasses import dataclass
from logzero import logger
import numpy as np
from vca.types import TRUnit
from BITS.clustering.seq import ClusteringSeq
from BITS.seq.align import EdlibRunner
from BITS.util.io import load_pickle, save_pickle
from BITS.util.proc import NoDaemonPool
from BITS.seq.utils import revcomp

In [10]:
def read_to_forward_units(read):
    """Return all units contained in <read> so that starnd of every unit is same as the forward master unit."""
    return [read.seq[unit.start:unit.end] if unit.id == 0 else revcomp(read.seq[unit.start:unit.end])
            for unit in read.units]

In [4]:
sync_reads = load_pickle("centromere_reads_incl_low_cover_rate_all_sync.pkl")

In [43]:
len(sync_reads)

1905

In [8]:
sync_units = []
for read in sync_reads:
    sync_units += read_to_forward_units(read)

In [9]:
len(sync_units)

46538

In [ ]:
centromere_phreds = load_pickle("centromere_phreds_incl_low_cover_rate_all_sync.pkl")

In [ ]:
sync_quals = []
for read in sync_reads:
    sync_quals += [centromere_phreds[read.name][unit.start:unit.end] if unit.id == 0
                   else np.flip(centromere_phreds[read.name][unit.start:unit.end])
                   for unit in read.units]

-> この数ではクラスタリングも厳しい。

In [51]:
db_prefix = "DMEL_CSS"
db_fname = f"{db_prefix}.db"
las_fname = f"TAN.{db_prefix}.las"
from vca import ReadViewer
v = ReadViewer(db_fname, las_fname)

In [59]:
sync_reads_by_id = {read.id: read for read in sync_reads}

In [29]:
v.show(read=sync_reads_by_id[73])

[I 190919 19:02:33 log:17] Starting distance matrix calculation 
[I 190919 19:02:33 log:19] Finished distance matrix calculation


In [28]:
sync_reads_by_id[762]

TRRead(seq='aaatccttcaaaaagtgatagtaatcgttagcgctggtaataagctgttaaaaaccgttattcttacatctatatgaccattttagccgagtaatgacgaaaattccgattgtaaatatcaacttttaggcaaaatccgtttttccaaatttcggtcatcaaataatcagttttttttttttgccacaactttataaatatttgtctgaatacggaatgtcatacttcgctgagctcgtaattacatttacaattaaaatgtgttcaaaaatggaaattatgtttttttgccatacttttcaaatttttatggggggtcattacaaaaaatacgaaaatttacccaaaaattgatttccctaaatccttcaataagtgatagtaatcgttagcgctggtaataagctgttaaaaaccgttattcttacatctatatgaccattttagccgagtaatgacgaaaattccgtttgtaaatatcaactttttggcaaaatccgtttttccaaatttcggtcatcaaataatcagttttttttttgccacaactttataaatatttgtctgaatacggaatgtcatacctcgctgagctcgtaattacatttaaaattaaaatgtgttcaaaaatggaaattatgttttttgccatactttgcaaatttttatggggggtcattacaaaaaatacgaaatttgacccaaatattgatttccctaaatccttcaaaaagtgatagtaatcgttagcgctggtaataagctgttaaaaaccgttattcttacatctatatgaccattttagccgagtaatgacgaaaattccgattgtaaatatcaacttttaggcaaaatccgttttttccaaatttcggtcatcaaataatcagtttttttttttttgccacaactttataaatatttgtctgaatacggaatgtcatacttcgctgagctcgtaattacatttacaattaaaatgtgttca

In [78]:
!(cat master_unit)

caaaaatgttgatatttacaaacgaaattttcgttataacttggctaaaaatggtcacatagatgtaagaataactgttttgagcagctaattaccagtgctaacgatccctattactttttgaaggatttagggaaattaatttttggatcaattttcgcattttttgtaaggaggggggtcatcaaaatttgcaaaatatggccaaaaaatttaatttccatttttgaacacagtttgattggaaattttattacgagctcagtgaggtatgacattccatattcagacaattattttttatgttgtggcaaaataaatgattatttgatgaccgaaatttggaaaaacagactctg


In [14]:
master_unit = "caaaaatgttgatatttacaaacgaaattttcgttataacttggctaaaaatggtcacatagatgtaagaataactgttttgagcagctaattaccagtgctaacgatccctattactttttgaaggatttagggaaattaatttttggatcaattttcgcattttttgtaaggaggggggtcatcaaaatttgcaaaatatggccaaaaaatttaatttccatttttgaacacagtttgattggaaattttattacgagctcagtgaggtatgacattccatattcagacaattattttttatgttgtggcaaaataaatgattatttgatgaccgaaatttggaaaaacagactctg"

## Functions for counting variants

In [5]:
# Variants and sequencing errors

class PairwiseAlignment:
    def __init__(self, a_seq, b_seq):
        er = EdlibRunner("global", revcomp=False, cyclic=False)
        self.fcigar = er.align(b_seq.lower(), a_seq.lower()).cigar.flatten().string   # NOTE: b vs a; be careful!
        self.source, self.target = '', ''
        s_pos, t_pos = 0, 0
        for c in self.fcigar:
            if c == '=' or c == 'X':
                self.source += a_seq[s_pos]
                self.target += b_seq[t_pos]
                s_pos += 1
                t_pos += 1
            elif c == 'I':
                self.source += '-'
                self.target += b_seq[t_pos]
                t_pos += 1
            else:
                self.source += a_seq[s_pos]
                self.target += '-'
                s_pos += 1
        
    def show(self, by_cigar=False):
        if by_cigar:   # standard alignment like BLAST
            print(self.source)
            print(self.fcigar)
            print(self.target)
        else:
            print(''.join([' ' if c == '=' else self.source[i] for i, c in enumerate(self.fcigar)]))
            print(''.join([self.source[i] if c == '=' else ' ' for i, c in enumerate(self.fcigar)]))
            print(''.join([' ' if c == '=' else self.target[i] for i, c in enumerate(self.fcigar)]))

def count_variants(cluster_cons_unit, cluster_units):
    """Given a set of unit sequences <units> in a cluster, calculate the composition of
    nucleotides including '-' (= distribution of each )
    for each position on <cluster_cons_unit> as a seed.
    from which <units> are generated, compute the variations (= nucleotides inconsistent between
    <units> and <cluster_cons_unit> and their relative frequency).
    Since a cluster should be homogeneous (i.e., mono-source), the relative frequencies are
    expected to be not much larger than sequencing error.
    """
    assert cluster_cons_unit != "", "Empty strings are not allowed"
    # TODO: how to decide "same variant?" especially for multiple variations on same position (but slightly different among units)?
    variants = Counter()
    for unit in cluster_units:
        assert unit != "", "Empty strings are not allowed"
        alignment = PairwiseAlignment(cluster_cons_unit, unit)   # alignment.fcigar(cluster_cons_unit) = unit
        tpos = 0
        var_index = 0   # positive values for continuous insertions
        for i, c in enumerate(alignment.fcigar):
            if c == '=':
                var_index = 0
            elif c == 'I':
                var_index += 1
            if c != '=':
                variants[(tpos, var_index, c, alignment.target[i])] += 1   # TODO: multiple D on the same pos are aggregated
            if c != 'I':
                tpos += 1
        assert tpos == len(cluster_cons_unit)
    return variants

def list_variations(template_unit, cluster_cons_unit):
    """Single-vs-single version of count_variants().
    That is, list up the differences between the (imaginary) template unit and the consensus unit
    of a cluster (which should be a real instance).
    The return value is [(position_on_template_unit, variant_type, base_on_cluster_cons_unit)].
    """
    assert template_unit != "" and cluster_cons_unit != "", "Empty strings are not allowed"
    return list(count_variants(template_unit, [cluster_cons_unit]).keys())

## Convert a read to a unit spectrum (= consensus units & variants)

上は任意の intra-read repr unit 用、下は forward master unit の上での spectrum

In [16]:
def characterize_sync_read(read, min_var_frac=0.1):
    """Convert a synchronized read into a set of representative units and variants within them."""
    # TODO: window size and slide   # TODO: min_var_count in a window rather than min_var_frac in a read?
    read_spectrum = []

    # Call variants with relative frequency >= <min_var_frac>
    for repr_id, repr_unit in read.repr_units.items():
        units = [read.seq[unit.start:unit.end] for unit in read.units if unit.id == repr_id]
        if len(units) < 5:
            continue
        var_counts = sorted(count_variants(repr_unit, units).items())
        var_counts = [(key, round(count / len(units), 3)) for key, count in var_counts]
        
        logger.debug(f"#units = {len(units)}, min var freq = {round(len(units) * min_var_frac, 3)}")
        var_counts = tuple(filter(lambda x: x[1] >= min_var_frac, var_counts))
        read_spectrum.append((repr_unit, var_counts))

    return read_spectrum

def characterize_sync_read_forward(read, min_n_units=5, min_var_frac=0.1):   # restrict to only forward master unit
    """Convert a synchronized read into a set of representative units and variants within them."""
    # TODO: window size and slide   # TODO: min_var_count in a window rather than min_var_frac in a read?
    
    units = read_to_forward_units(read)
    if len(units) < min_n_units:
        return None
    var_counts = sorted(count_variants(master_unit, units).items())
    var_freqs = [(key, round(count / len(units), 3)) for key, count in var_counts]

    logger.debug(f"#units = {len(units)}, min var freq = {round(len(units) * min_var_frac, 3)}")
    return tuple(filter(lambda x: x[1] >= min_var_frac, var_freqs))

In [24]:
# 任意の repr unit の場合
for i in range(5):
    print(characterize_sync_read(sync_reads[i]))

[D 190919 21:08:33 <ipython-input-16-2bf705a8ecd4>:14] #units = 38, min var freq = 3.8
[D 190919 21:08:33 <ipython-input-16-2bf705a8ecd4>:14] #units = 12, min var freq = 1.2
[D 190919 21:08:33 <ipython-input-16-2bf705a8ecd4>:14] #units = 16, min var freq = 1.6
[D 190919 21:08:33 <ipython-input-16-2bf705a8ecd4>:14] #units = 36, min var freq = 3.6
[D 190919 21:08:33 <ipython-input-16-2bf705a8ecd4>:14] #units = 32, min var freq = 3.2


[('cagagtctgtttttccaaatttcggtcatcaaataatcatttattttgccacaacataaaaaataattgtctgaatatggaatgtcatacctcactgagctcgtaataaaatttccaatcaaactgtgttcaaaaatggaaattaaattttttggccatattttgcaaattttgatgacccccctccttacaaaaaatgcgaaaattgatccaaaaattaatttccctaaatccttcaaaaagtaatagggatcgttagcactggtaattagctgctcaaaacagttattcttacatctatgtgaccatttttagccaagttataacgaaaatttcgtttgtaaatatcaacatttttg', (((4, 0, 'X', 'a'), 0.211), ((18, 0, 'X', 't'), 0.132), ((33, 0, 'D', '-'), 0.132), ((33, 0, 'X', 'a'), 0.237), ((75, 0, 'X', 'c'), 0.184), ((93, 0, 'X', 't'), 0.316), ((116, 0, 'X', 'c'), 0.184), ((142, 0, 'X', 'c'), 0.132), ((152, 0, 'X', 'g'), 0.263), ((156, 0, 'D', '-'), 0.132), ((159, 1, 'I', 't'), 0.132), ((163, 0, 'X', 'g'), 0.368), ((173, 0, 'X', 'c'), 0.237), ((180, 0, 'X', 'a'), 0.184), ((183, 0, 'X', 't'), 0.158), ((186, 0, 'D', '-'), 0.184), ((205, 0, 'X', 'g'), 0.316), ((208, 0, 'X', 'g'), 0.237), ((210, 0, 'X', 't'), 0.368), ((226, 0, 'D', '-'), 0.526), ((246, 0, 'X', 'c'), 0.184), ((249, 0, 'X', 'a'), 0.368), ((2

In [17]:
# forward master unit だけの場合
for i in range(5):
    print(characterize_sync_read_forward(sync_reads[i]))

[D 190919 21:05:40 <ipython-input-16-2bf705a8ecd4>:30] #units = 38, min var freq = 3.8
[D 190919 21:05:40 <ipython-input-16-2bf705a8ecd4>:30] #units = 12, min var freq = 1.2
[D 190919 21:05:40 <ipython-input-16-2bf705a8ecd4>:30] #units = 16, min var freq = 1.6
[D 190919 21:05:40 <ipython-input-16-2bf705a8ecd4>:30] #units = 36, min var freq = 3.6
[D 190919 21:05:40 <ipython-input-16-2bf705a8ecd4>:30] #units = 32, min var freq = 3.2


(((5, 0, 'D', '-'), 0.211), ((9, 0, 'X', 'a'), 0.211), ((21, 0, 'X', 'c'), 0.316), ((23, 0, 'D', '-'), 0.316), ((47, 0, 'X', 'g'), 0.237), ((48, 0, 'X', 'c'), 0.237), ((52, 0, 'X', 't'), 0.368), ((67, 0, 'X', 'c'), 0.447), ((68, 0, 'X', 'c'), 0.395), ((73, 0, 'X', 't'), 0.447), ((81, 0, 'X', 'a'), 0.395), ((88, 0, 'X', 'a'), 0.184), ((109, 0, 'X', 't'), 0.368), ((112, 0, 'X', 'g'), 0.184), ((134, 0, 'D', '-'), 0.526), ((148, 0, 'X', 'a'), 0.368), ((150, 0, 'X', 'c'), 0.237), ((153, 0, 'X', 'c'), 0.316), ((173, 0, 'X', 'a'), 0.158), ((178, 0, 'X', 't'), 0.184), ((180, 0, 'D', '-'), 0.211), ((185, 0, 'X', 'g'), 0.237), ((195, 0, 'X', 'c'), 0.368), ((201, 1, 'I', 'a'), 0.132), ((203, 0, 'D', '-'), 0.132), ((206, 0, 'X', 'c'), 0.263), ((216, 0, 'X', 'g'), 0.132), ((242, 0, 'X', 'g'), 0.184), ((265, 0, 'X', 'a'), 0.316), ((283, 0, 'X', 'g'), 0.184), ((325, 0, 'D', '-'), 0.132), ((325, 0, 'X', 't'), 0.237), ((340, 0, 'X', 'a'), 0.132), ((354, 0, 'X', 't'), 0.211))
(((4, 0, 'X', 'g'), 0.25), 

問題は、このスペクトラム同士を比較する際にも、

- representative units 同士の phase synchronization が必要
- overlap している領域によってスペクトラムが変わる

という点である。

## Convert a unit spectrum to a unit sequence composition

In [19]:
import itertools

In [20]:
# define ambigous bases

bases = sorted(['a', 'c', 'g', 't', '-'])
powerset = []
for i in range(len(bases) + 1):
    powerset += list(itertools.combinations(bases, i))
powerset = powerset[1:]

map_bases_to_char = {}
for i, s in enumerate(powerset):
    map_bases_to_char[s] = chr(97 + i)
map_bases_to_char[tuple(bases)] = '='   # 2-byte char is not allow in edlib

In [21]:
map_bases_to_char

{('-',): 'a',
 ('a',): 'b',
 ('c',): 'c',
 ('g',): 'd',
 ('t',): 'e',
 ('-', 'a'): 'f',
 ('-', 'c'): 'g',
 ('-', 'g'): 'h',
 ('-', 't'): 'i',
 ('a', 'c'): 'j',
 ('a', 'g'): 'k',
 ('a', 't'): 'l',
 ('c', 'g'): 'm',
 ('c', 't'): 'n',
 ('g', 't'): 'o',
 ('-', 'a', 'c'): 'p',
 ('-', 'a', 'g'): 'q',
 ('-', 'a', 't'): 'r',
 ('-', 'c', 'g'): 's',
 ('-', 'c', 't'): 't',
 ('-', 'g', 't'): 'u',
 ('a', 'c', 'g'): 'v',
 ('a', 'c', 't'): 'w',
 ('a', 'g', 't'): 'x',
 ('c', 'g', 't'): 'y',
 ('-', 'a', 'c', 'g'): 'z',
 ('-', 'a', 'c', 't'): '{',
 ('-', 'a', 'g', 't'): '|',
 ('-', 'c', 'g', 't'): '}',
 ('a', 'c', 'g', 't'): '~',
 ('-', 'a', 'c', 'g', 't'): '='}

下の関数は任意の spectrum 用で、forward master unit に限定した場合は variant set を比較するだけなので不要。

In [22]:
def revcomp_spec(spec):
    repr_seq, var_freqs = spec
    repr_seq = revcomp(repr_seq)
    var_freqs = tuple([((len(repr_seq) - pos if op == 'I' else len(repr_seq) - 1 - pos, index, op, revcomp(base)), freq)
                       for (pos, index, op, base), freq in reversed(var_freqs)])   # Be careful for insertion position
    return (repr_seq, var_freqs)

def spec_to_comp(spec):
    seed_seq, var_freqs = spec
    comp_seq = ""
    
    insertions = defaultdict(set)
    others = defaultdict(set)
    for (pos, index, op, base), freq in var_freqs:
        if op == 'I':
            insertions[(pos, index)].add(base)
        else:
            others[pos].add(base)
    
    # Process each position
    for pos, seed_base in enumerate(seed_seq):
        # First add insertions with '-'
        if (pos, 1) in insertions:
            index = 1
            while (pos, index) in insertions:
                bases = insertions[(pos, index)]
                bases.add('-')   # on seed
                comp_seq += map_bases_to_char[tuple(sorted(bases))]
                index += 1
        # Next add the other variants with seed base
        bases = others[pos]   # empty set if not exist
        bases.add(seed_base)
        comp_seq += map_bases_to_char[tuple(sorted(bases))]
    # Add insertions at the end of <seed_seq>
    if (len(seed_seq), 1) in insertions:
        index = 1
        while (len(seed_seq), index) in insertions:
            bases = insertions[(len(seed_seq), index)]
            bases.add('-')   # on seed
            comp_seq += map_bases_to_char[tuple(sorted(bases))]
            index += 1
            
    return comp_seq

In [23]:
# 任意の repr unit の場合
spec_to_comp(characterize_sync_read(sync_reads[0])[0])

[D 190919 21:08:22 <ipython-input-16-2bf705a8ecd4>:14] #units = 38, min var freq = 3.8


'cbdbkecedeeeeeccbbleeecddecbecbbbrbbecbeeebeeeedccbcbbcbebbbbbbebbeedecedbbnbeddbbedecbebcceclcedbdcecdebbebbbbeeeccjbecbbbcededeecbbbbbeddbbbnebbbeeeeeoddcgbeibeeeodcbbbeeeembedbccjccnecgeebcbbbbbbedcdbbbboedkencbbbbbeebbeeeccgebbbecceecbbbbbdebbnbdkdbecdeebdcbceddebbeeldcedcenbbbbcbdlebeemoebcbecebededbcjbeeonebdccbbdeebebbcdbbbbeeemdeeidebbbebeclbcbeeeeid'

In [25]:
EdlibRunner("global", revcomp=False, cyclic=True).align(spec_to_comp(characterize_sync_read(sync_reads[0])[0]),
                                                        spec_to_comp(characterize_sync_read(sync_reads[1])[0]))

[D 190919 21:09:26 <ipython-input-16-2bf705a8ecd4>:14] #units = 38, min var freq = 3.8
[D 190919 21:09:26 <ipython-input-16-2bf705a8ecd4>:14] #units = 12, min var freq = 1.2


q[None:None] vs t[0:363]   (363 bp, 13.2% diff)

## Compute alignment between two unit spectra by their unit compositions

In [41]:
def align_read_by_spectrum(a_spec, b_spec):
    """Compute alignment between two read spectrum <a_spec> and <b_spec>.
    This is a generalized pairwise alignment of sequence composition.
    """
    a_comp_seq = spec_to_comp(a_spec)
    b_comp_seq = spec_to_comp(b_spec)
    
    er = EdlibRunner("global", revcomp=False, cyclic=True)
    diff = er.align(a_comp_seq, b_comp_seq).diff
    if diff > 0.2:
        b_comp_seq_rc = spec_to_comp(revcomp_spec(b_spec))
        diff_rc = er.align(a_comp_seq, b_comp_seq_rc).diff
        if diff > diff_rc:
            diff = diff_rc
        
    return round(diff * 100, 3)

def align_read_by_spectrum_forward(a_var_freqs, b_var_freqs):   # restricted to only forward master unit
    """Compute alignment between two read spectrum <a_spec> and <b_spec>.
    This is a generalized pairwise alignment of sequence composition.
    """
    a_vars = set(dict(a_var_freqs).keys())
    b_vars = set(dict(b_var_freqs).keys())
    diff = 1 - len(a_vars & b_vars) / len(a_vars | b_vars)

    return round(diff * 100, 3)

### Result of compositions using forward master unit

In [43]:
# forward master unit
sync_read_var_freqs = [(read.id, characterize_sync_read_forward(read)) for read in sync_reads]

[D 190919 21:17:14 <ipython-input-16-2bf705a8ecd4>:30] #units = 38, min var freq = 3.8
[D 190919 21:17:14 <ipython-input-16-2bf705a8ecd4>:30] #units = 12, min var freq = 1.2
[D 190919 21:17:14 <ipython-input-16-2bf705a8ecd4>:30] #units = 16, min var freq = 1.6
[D 190919 21:17:15 <ipython-input-16-2bf705a8ecd4>:30] #units = 36, min var freq = 3.6
[D 190919 21:17:15 <ipython-input-16-2bf705a8ecd4>:30] #units = 32, min var freq = 3.2
[D 190919 21:17:15 <ipython-input-16-2bf705a8ecd4>:30] #units = 28, min var freq = 2.8
[D 190919 21:17:15 <ipython-input-16-2bf705a8ecd4>:30] #units = 35, min var freq = 3.5
[D 190919 21:17:15 <ipython-input-16-2bf705a8ecd4>:30] #units = 39, min var freq = 3.9
[D 190919 21:17:15 <ipython-input-16-2bf705a8ecd4>:30] #units = 32, min var freq = 3.2
[D 190919 21:17:15 <ipython-input-16-2bf705a8ecd4>:30] #units = 34, min var freq = 3.4
[D 190919 21:17:15 <ipython-input-16-2bf705a8ecd4>:30] #units = 17, min var freq = 1.7
[D 190919 21:17:15 <ipython-input-16-2bf705

[D 190919 21:17:16 <ipython-input-16-2bf705a8ecd4>:30] #units = 32, min var freq = 3.2
[D 190919 21:17:16 <ipython-input-16-2bf705a8ecd4>:30] #units = 28, min var freq = 2.8
[D 190919 21:17:16 <ipython-input-16-2bf705a8ecd4>:30] #units = 22, min var freq = 2.2
[D 190919 21:17:16 <ipython-input-16-2bf705a8ecd4>:30] #units = 22, min var freq = 2.2
[D 190919 21:17:16 <ipython-input-16-2bf705a8ecd4>:30] #units = 11, min var freq = 1.1
[D 190919 21:17:16 <ipython-input-16-2bf705a8ecd4>:30] #units = 29, min var freq = 2.9
[D 190919 21:17:16 <ipython-input-16-2bf705a8ecd4>:30] #units = 39, min var freq = 3.9
[D 190919 21:17:16 <ipython-input-16-2bf705a8ecd4>:30] #units = 25, min var freq = 2.5
[D 190919 21:17:16 <ipython-input-16-2bf705a8ecd4>:30] #units = 23, min var freq = 2.3
[D 190919 21:17:16 <ipython-input-16-2bf705a8ecd4>:30] #units = 30, min var freq = 3.0
[D 190919 21:17:16 <ipython-input-16-2bf705a8ecd4>:30] #units = 38, min var freq = 3.8
[D 190919 21:17:16 <ipython-input-16-2bf705

[D 190919 21:17:17 <ipython-input-16-2bf705a8ecd4>:30] #units = 31, min var freq = 3.1
[D 190919 21:17:17 <ipython-input-16-2bf705a8ecd4>:30] #units = 30, min var freq = 3.0
[D 190919 21:17:17 <ipython-input-16-2bf705a8ecd4>:30] #units = 21, min var freq = 2.1
[D 190919 21:17:17 <ipython-input-16-2bf705a8ecd4>:30] #units = 32, min var freq = 3.2
[D 190919 21:17:17 <ipython-input-16-2bf705a8ecd4>:30] #units = 31, min var freq = 3.1
[D 190919 21:17:17 <ipython-input-16-2bf705a8ecd4>:30] #units = 35, min var freq = 3.5
[D 190919 21:17:17 <ipython-input-16-2bf705a8ecd4>:30] #units = 17, min var freq = 1.7
[D 190919 21:17:17 <ipython-input-16-2bf705a8ecd4>:30] #units = 37, min var freq = 3.7
[D 190919 21:17:17 <ipython-input-16-2bf705a8ecd4>:30] #units = 34, min var freq = 3.4
[D 190919 21:17:17 <ipython-input-16-2bf705a8ecd4>:30] #units = 36, min var freq = 3.6
[D 190919 21:17:18 <ipython-input-16-2bf705a8ecd4>:30] #units = 36, min var freq = 3.6
[D 190919 21:17:18 <ipython-input-16-2bf705

[D 190919 21:17:19 <ipython-input-16-2bf705a8ecd4>:30] #units = 16, min var freq = 1.6
[D 190919 21:17:19 <ipython-input-16-2bf705a8ecd4>:30] #units = 34, min var freq = 3.4
[D 190919 21:17:19 <ipython-input-16-2bf705a8ecd4>:30] #units = 31, min var freq = 3.1
[D 190919 21:17:19 <ipython-input-16-2bf705a8ecd4>:30] #units = 16, min var freq = 1.6
[D 190919 21:17:19 <ipython-input-16-2bf705a8ecd4>:30] #units = 35, min var freq = 3.5
[D 190919 21:17:19 <ipython-input-16-2bf705a8ecd4>:30] #units = 36, min var freq = 3.6
[D 190919 21:17:19 <ipython-input-16-2bf705a8ecd4>:30] #units = 31, min var freq = 3.1
[D 190919 21:17:19 <ipython-input-16-2bf705a8ecd4>:30] #units = 20, min var freq = 2.0
[D 190919 21:17:19 <ipython-input-16-2bf705a8ecd4>:30] #units = 36, min var freq = 3.6
[D 190919 21:17:19 <ipython-input-16-2bf705a8ecd4>:30] #units = 20, min var freq = 2.0
[D 190919 21:17:19 <ipython-input-16-2bf705a8ecd4>:30] #units = 34, min var freq = 3.4
[D 190919 21:17:19 <ipython-input-16-2bf705

[D 190919 21:17:20 <ipython-input-16-2bf705a8ecd4>:30] #units = 32, min var freq = 3.2
[D 190919 21:17:20 <ipython-input-16-2bf705a8ecd4>:30] #units = 29, min var freq = 2.9
[D 190919 21:17:20 <ipython-input-16-2bf705a8ecd4>:30] #units = 30, min var freq = 3.0
[D 190919 21:17:20 <ipython-input-16-2bf705a8ecd4>:30] #units = 23, min var freq = 2.3
[D 190919 21:17:20 <ipython-input-16-2bf705a8ecd4>:30] #units = 36, min var freq = 3.6
[D 190919 21:17:20 <ipython-input-16-2bf705a8ecd4>:30] #units = 33, min var freq = 3.3
[D 190919 21:17:20 <ipython-input-16-2bf705a8ecd4>:30] #units = 27, min var freq = 2.7
[D 190919 21:17:20 <ipython-input-16-2bf705a8ecd4>:30] #units = 14, min var freq = 1.4
[D 190919 21:17:20 <ipython-input-16-2bf705a8ecd4>:30] #units = 36, min var freq = 3.6
[D 190919 21:17:20 <ipython-input-16-2bf705a8ecd4>:30] #units = 13, min var freq = 1.3
[D 190919 21:17:20 <ipython-input-16-2bf705a8ecd4>:30] #units = 34, min var freq = 3.4
[D 190919 21:17:20 <ipython-input-16-2bf705

...

[D 190919 21:17:32 <ipython-input-16-2bf705a8ecd4>:30] #units = 16, min var freq = 1.6
[D 190919 21:17:32 <ipython-input-16-2bf705a8ecd4>:30] #units = 35, min var freq = 3.5
[D 190919 21:17:32 <ipython-input-16-2bf705a8ecd4>:30] #units = 12, min var freq = 1.2
[D 190919 21:17:32 <ipython-input-16-2bf705a8ecd4>:30] #units = 34, min var freq = 3.4
[D 190919 21:17:32 <ipython-input-16-2bf705a8ecd4>:30] #units = 31, min var freq = 3.1
[D 190919 21:17:32 <ipython-input-16-2bf705a8ecd4>:30] #units = 34, min var freq = 3.4
[D 190919 21:17:32 <ipython-input-16-2bf705a8ecd4>:30] #units = 23, min var freq = 2.3
[D 190919 21:17:32 <ipython-input-16-2bf705a8ecd4>:30] #units = 32, min var freq = 3.2
[D 190919 21:17:32 <ipython-input-16-2bf705a8ecd4>:30] #units = 32, min var freq = 3.2
[D 190919 21:17:32 <ipython-input-16-2bf705a8ecd4>:30] #units = 30, min var freq = 3.0
[D 190919 21:17:33 <ipython-input-16-2bf705a8ecd4>:30] #units = 35, min var freq = 3.5
[D 190919 21:17:33 <ipython-input-16-2bf705

[D 190919 21:17:34 <ipython-input-16-2bf705a8ecd4>:30] #units = 12, min var freq = 1.2
[D 190919 21:17:34 <ipython-input-16-2bf705a8ecd4>:30] #units = 14, min var freq = 1.4
[D 190919 21:17:34 <ipython-input-16-2bf705a8ecd4>:30] #units = 30, min var freq = 3.0
[D 190919 21:17:34 <ipython-input-16-2bf705a8ecd4>:30] #units = 12, min var freq = 1.2
[D 190919 21:17:34 <ipython-input-16-2bf705a8ecd4>:30] #units = 32, min var freq = 3.2
[D 190919 21:17:34 <ipython-input-16-2bf705a8ecd4>:30] #units = 31, min var freq = 3.1
[D 190919 21:17:34 <ipython-input-16-2bf705a8ecd4>:30] #units = 36, min var freq = 3.6
[D 190919 21:17:34 <ipython-input-16-2bf705a8ecd4>:30] #units = 17, min var freq = 1.7
[D 190919 21:17:34 <ipython-input-16-2bf705a8ecd4>:30] #units = 10, min var freq = 1.0
[D 190919 21:17:34 <ipython-input-16-2bf705a8ecd4>:30] #units = 34, min var freq = 3.4
[D 190919 21:17:34 <ipython-input-16-2bf705a8ecd4>:30] #units = 37, min var freq = 3.7
[D 190919 21:17:34 <ipython-input-16-2bf705

[D 190919 21:17:35 <ipython-input-16-2bf705a8ecd4>:30] #units = 26, min var freq = 2.6
[D 190919 21:17:35 <ipython-input-16-2bf705a8ecd4>:30] #units = 28, min var freq = 2.8
[D 190919 21:17:35 <ipython-input-16-2bf705a8ecd4>:30] #units = 29, min var freq = 2.9
[D 190919 21:17:35 <ipython-input-16-2bf705a8ecd4>:30] #units = 24, min var freq = 2.4
[D 190919 21:17:35 <ipython-input-16-2bf705a8ecd4>:30] #units = 18, min var freq = 1.8
[D 190919 21:17:35 <ipython-input-16-2bf705a8ecd4>:30] #units = 20, min var freq = 2.0
[D 190919 21:17:35 <ipython-input-16-2bf705a8ecd4>:30] #units = 18, min var freq = 1.8
[D 190919 21:17:35 <ipython-input-16-2bf705a8ecd4>:30] #units = 27, min var freq = 2.7
[D 190919 21:17:35 <ipython-input-16-2bf705a8ecd4>:30] #units = 34, min var freq = 3.4
[D 190919 21:17:35 <ipython-input-16-2bf705a8ecd4>:30] #units = 26, min var freq = 2.6
[D 190919 21:17:35 <ipython-input-16-2bf705a8ecd4>:30] #units = 37, min var freq = 3.7
[D 190919 21:17:35 <ipython-input-16-2bf705

[D 190919 21:17:36 <ipython-input-16-2bf705a8ecd4>:30] #units = 35, min var freq = 3.5
[D 190919 21:17:36 <ipython-input-16-2bf705a8ecd4>:30] #units = 15, min var freq = 1.5
[D 190919 21:17:36 <ipython-input-16-2bf705a8ecd4>:30] #units = 26, min var freq = 2.6
[D 190919 21:17:36 <ipython-input-16-2bf705a8ecd4>:30] #units = 36, min var freq = 3.6
[D 190919 21:17:37 <ipython-input-16-2bf705a8ecd4>:30] #units = 30, min var freq = 3.0
[D 190919 21:17:37 <ipython-input-16-2bf705a8ecd4>:30] #units = 20, min var freq = 2.0
[D 190919 21:17:37 <ipython-input-16-2bf705a8ecd4>:30] #units = 17, min var freq = 1.7
[D 190919 21:17:37 <ipython-input-16-2bf705a8ecd4>:30] #units = 21, min var freq = 2.1
[D 190919 21:17:37 <ipython-input-16-2bf705a8ecd4>:30] #units = 37, min var freq = 3.7
[D 190919 21:17:37 <ipython-input-16-2bf705a8ecd4>:30] #units = 32, min var freq = 3.2
[D 190919 21:17:37 <ipython-input-16-2bf705a8ecd4>:30] #units = 36, min var freq = 3.6
[D 190919 21:17:37 <ipython-input-16-2bf705

[D 190919 21:17:38 <ipython-input-16-2bf705a8ecd4>:30] #units = 34, min var freq = 3.4
[D 190919 21:17:38 <ipython-input-16-2bf705a8ecd4>:30] #units = 16, min var freq = 1.6
[D 190919 21:17:38 <ipython-input-16-2bf705a8ecd4>:30] #units = 24, min var freq = 2.4
[D 190919 21:17:38 <ipython-input-16-2bf705a8ecd4>:30] #units = 34, min var freq = 3.4
[D 190919 21:17:38 <ipython-input-16-2bf705a8ecd4>:30] #units = 11, min var freq = 1.1
[D 190919 21:17:38 <ipython-input-16-2bf705a8ecd4>:30] #units = 16, min var freq = 1.6
[D 190919 21:17:38 <ipython-input-16-2bf705a8ecd4>:30] #units = 31, min var freq = 3.1
[D 190919 21:17:38 <ipython-input-16-2bf705a8ecd4>:30] #units = 31, min var freq = 3.1
[D 190919 21:17:38 <ipython-input-16-2bf705a8ecd4>:30] #units = 33, min var freq = 3.3
[D 190919 21:17:38 <ipython-input-16-2bf705a8ecd4>:30] #units = 17, min var freq = 1.7
[D 190919 21:17:38 <ipython-input-16-2bf705a8ecd4>:30] #units = 18, min var freq = 1.8
[D 190919 21:17:38 <ipython-input-16-2bf705

In [44]:
len(sync_read_var_freqs)

1905

In [45]:
sync_read_var_freqs = list(filter(lambda x: x[1] is not None, sync_read_var_freqs))

In [46]:
len(sync_read_var_freqs)   # after remove reads with < 5 units

1665

In [65]:
comp_diffs = []
#for i in range(len(sync_reads)):
i = 0
read_id_i, var_freqs_i = sync_read_var_freqs[i]
for j in range(len(sync_read_var_freqs)):
    if i == j:
        continue
    read_id_j, var_freqs_j = sync_read_var_freqs[j]
    logger.debug(f"read {read_id_i} vs {read_id_j}")
    comp_diff = align_read_by_spectrum_forward(var_freqs_i, var_freqs_j)
    logger.debug(comp_diff)
    comp_diffs.append((comp_diff, i, read_id_i, j, read_id_j))

[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 123
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:11] 80.645
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 236
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:11] 80.303
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 300
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:11] 94.521
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 369
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:11] 80.645
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 395
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:11] 86.765
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 546
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:11] 82.353
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 559
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:11] 92.0
[I 190919 21:28:38 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 738
[I 190919 21:28:

[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 87.931
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 9973
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 81.356
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 9998
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 82.692
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 10305
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 79.545
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 10757
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 79.63
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 10827
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 83.051
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 10846
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 88.525
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 11160
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 52.174
[I 190919 

[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 69.091
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 22844
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 92.0
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 23043
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 83.824
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 23160
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 94.737
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 23270
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 93.617
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 23271
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 88.75
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 23402
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 91.667
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 23489
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 83.333
[I 190919 

[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 87.037
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 38153
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 95.745
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 38512
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 80.357
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 39104
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 89.286
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 39575
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 96.875
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 39760
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 63.415
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 39816
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 95.0
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 41012
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 75.556
[I 190919

[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 85.246
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 61741
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 85.455
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 62061
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 92.308
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 62272
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 86.885
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 62454
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 93.056
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 62516
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 86.538
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 62627
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 84.483
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 62923
[I 190919 21:28:39 <ipython-input-65-c1bda37cdd45>:11] 84.615
[I 1909

...

[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 89.286
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 357146
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 82.0
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 357678
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 86.0
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 358377
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 84.615
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 358542
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 97.727
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 358790
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 84.127
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 359035
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 95.556
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 359531
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 88.406
[I 1

[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 375085
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 94.595
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 375483
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 82.857
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 375838
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 87.097
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 376281
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 92.857
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 376660
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 94.318
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 377011
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 93.913
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 377354
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 96.552
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 

[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 77.273
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 390693
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 91.935
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 390777
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 90.909
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 390945
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 43.902
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 391147
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 81.967
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 391581
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 90.741
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 391654
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 85.938
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 391826
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 84.615


[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 411062
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 86.765
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 411237
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 84.615
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 411275
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 90.141
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 411371
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 83.333
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 411658
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 92.647
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 412250
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 83.607
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 412471
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:11] 83.051
[I 190919 21:28:41 <ipython-input-65-c1bda37cdd45>:9] read 73 

[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:11] 81.818
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 427803
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:11] 82.54
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 427851
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:11] 81.356
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 428406
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:11] 84.615
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 428556
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:11] 96.296
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 428619
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:11] 88.889
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 428623
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:11] 88.679
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:9] read 73 vs 428650
[I 190919 21:28:42 <ipython-input-65-c1bda37cdd45>:11] 80.0
[I 

In [66]:
show_plot([make_hist([x[0] for x in comp_diffs], bin_size=1)])

In [67]:
sorted(comp_diffs)[:10]

[(5.556, 0, 73, 703, 198167),
 (18.421, 0, 73, 94, 16873),
 (18.919, 0, 73, 991, 271282),
 (23.077, 0, 73, 46, 7556),
 (24.39, 0, 73, 1516, 401347),
 (25.0, 0, 73, 663, 188060),
 (25.0, 0, 73, 1273, 338213),
 (25.641, 0, 73, 336, 90327),
 (25.641, 0, 73, 363, 96908),
 (26.19, 0, 73, 1253, 334044)]

In [60]:
v.show(read=sync_reads_by_id[73])

[I 190919 21:26:41 log:17] Starting distance matrix calculation 
[I 190919 21:26:41 log:19] Finished distance matrix calculation


In [61]:
v.show(read=sync_reads_by_id[198167])

[I 190919 21:26:58 log:17] Starting distance matrix calculation 
[I 190919 21:26:58 log:19] Finished distance matrix calculation


In [68]:
comp_diffs = []
#for i in range(len(sync_reads)):
i = 703
read_id_i, var_freqs_i = sync_read_var_freqs[i]
for j in range(len(sync_read_var_freqs)):
    if i == j:
        continue
    read_id_j, var_freqs_j = sync_read_var_freqs[j]
    logger.debug(f"read {read_id_i} vs {read_id_j}")
    comp_diff = align_read_by_spectrum_forward(var_freqs_i, var_freqs_j)
    logger.debug(comp_diff)
    comp_diffs.append((comp_diff, i, read_id_i, j, read_id_j))

[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 73
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 5.556
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 123
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 79.365
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 236
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 80.882
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 300
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 94.667
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 369
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 81.25
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 395
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 85.507
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 546
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 83.019
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read

[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 87.5
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 9396
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 94.898
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 9721
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 79.31
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 9731
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 88.333
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 9973
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 80.0
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 9998
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 83.333
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 10305
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 80.435
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 10757
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:

[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 97.826
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 22230
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 94.03
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 22306
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 96.939
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 22449
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 67.308
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 22603
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 91.304
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 22783
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 70.175
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 22844
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 92.308
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 23043
[I 190919 21:28:56 <ipython-input-68-53570

[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 88.608
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 36852
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 90.164
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 37405
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 55.556
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 37430
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 82.759
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 37532
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 91.549
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 37699
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 88.889
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 37952
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 89.157
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 38031
[I 190919 21:28:56 <ipython-input-68-5357

[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 96.0
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 56701
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 43.478
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 57089
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 85.714
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 57248
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 85.484
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 57309
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 91.935
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 57582
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 78.571
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 57607
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:11] 93.421
[I 190919 21:28:56 <ipython-input-68-535708c07fbf>:9] read 198167 vs 59001
[I 190919 21:28:56 <ipython-input-68-535708

...

[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 90.909
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 362199
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 60.784
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 362423
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 92.647
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 362878
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 91.071
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 363091
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 88.71
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 363324
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 95.876
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 363402
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 88.889
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 363406
[I 190919 21:28:58 <ipython-input-6

[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 87.5
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 379441
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 81.25
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 379453
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 75.0
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 380015
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 87.302
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 380214
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 85.965
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 380537
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 85.714
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 380697
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 87.5
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 380798
[I 190919 21:28:58 <ipython-input-68-5357

[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 82.456
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 394125
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 79.63
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 394209
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 86.111
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 394540
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 89.286
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 394585
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 83.333
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 394628
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 90.278
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 394666
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:11] 83.929
[I 190919 21:28:58 <ipython-input-68-535708c07fbf>:9] read 198167 vs 394694
[I 190919 21:28:58 <ipython-input-6

[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 414420
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 84.848
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 414664
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 81.356
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 414751
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 85.484
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 414908
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 83.333
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 415118
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 95.522
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 415124
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 53.061
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 415173
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 91.228
[I 190919 21:28:59 <ipython-input-

[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 82.456
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 429479
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 85.484
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 429598
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 92.537
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 429896
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 80.328
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 430169
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 85.0
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 430850
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 88.333
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 431042
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:11] 88.679
[I 190919 21:28:59 <ipython-input-68-535708c07fbf>:9] read 198167 vs 431609
[I 190919 21:28:59 <ipython-input-68

In [70]:
sorted(comp_diffs)[:10]

[(5.556, 703, 198167, 0, 73),
 (22.5, 703, 198167, 46, 7556),
 (22.5, 703, 198167, 94, 16873),
 (23.077, 703, 198167, 991, 271282),
 (25.0, 703, 198167, 336, 90327),
 (27.907, 703, 198167, 1516, 401347),
 (28.571, 703, 198167, 663, 188060),
 (28.571, 703, 198167, 1273, 338213),
 (29.268, 703, 198167, 363, 96908),
 (29.268, 703, 198167, 747, 211431)]

In [71]:
v.show(read=sync_reads_by_id[7556])

[I 190919 21:29:47 log:17] Starting distance matrix calculation 
[I 190919 21:29:47 log:19] Finished distance matrix calculation


In [72]:
v.show(read=sync_reads_by_id[16873])

[I 190919 21:41:14 log:17] Starting distance matrix calculation 
[I 190919 21:41:15 log:19] Finished distance matrix calculation


In [73]:
v.show(read=sync_reads_by_id[271282])

[I 190919 21:42:00 log:17] Starting distance matrix calculation 
[I 190919 21:42:00 log:19] Finished distance matrix calculation


In [74]:
v.show(read=sync_reads_by_id[90327])

[I 190919 21:42:46 log:17] Starting distance matrix calculation 
[I 190919 21:42:47 log:19] Finished distance matrix calculation


In [75]:
v.show(read=sync_reads_by_id[401347])

[I 190919 21:46:30 log:17] Starting distance matrix calculation 
[I 190919 21:46:30 log:19] Finished distance matrix calculation


## Conclusion

もっと local な feature でないとダメそう。